In [4]:
# ================================================================
#  Copper-Price Direction-of-Move Classification
#  • Baseline (“without”), tier 0·05, tier 0·10
#  • Models: LogReg, DecisionTree, RandomForest, SVM, HMM
#    + Ensembles: Voting, Stacking
# ================================================================
import pathlib, warnings, numpy as np, pandas as pd
from statsmodels.tsa.stattools import adfuller, coint, grangercausalitytests
from sklearn.model_selection import TimeSeriesSplit, KFold
from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import make_pipeline
from sklearn.linear_model import LogisticRegression
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import (RandomForestClassifier, VotingClassifier,
                              StackingClassifier)
from sklearn.svm import SVC
from hmmlearn.hmm import GaussianHMM
from sklearn.metrics import accuracy_score

warnings.filterwarnings("ignore")
pd.set_option("display.float_format", "{:,.4f}".format)
np.random.seed(42)

# ── 1. Load copper price and Google-Trends data ------------------
ROOT = pathlib.Path(".")
def load_copper(fp=ROOT / "Copper Prices.csv"):
    df = (pd.read_csv(fp)
            .assign(Date=lambda d: pd.to_datetime(d["Date"]))
            .set_index("Date")
            .asfreq("W-SUN"))
    return df["Price"].rename("Copper_Price")

def load_trends():
    def one_folder(folder):
        frames = []
        for fp in (ROOT / folder).glob("*.csv"):
            key = fp.stem.replace(",", "")
            t   = pd.read_csv(fp); t.columns = [c.strip() for c in t.columns]
            val = t.columns[1]
            frames.append(t.assign(Date=lambda d: pd.to_datetime(d[t.columns[0]]))
                            .set_index("Date")
                            .asfreq("W-SUN")
                            .rename(columns={val: key}))
        return pd.concat(frames, axis=1) if frames else pd.DataFrame()
    cats = ["Supply Factors", "Demand Factors",
            "Speculative Factors", "Sudden Factors"]
    return pd.concat([one_folder(c) for c in cats], axis=1).sort_index()

copper, trends = load_copper(), load_trends()
data_raw = pd.concat([copper, trends], axis=1).dropna()

# ── 2. ADF to find I(1) series -----------------------------------
ALPHA_ADF, ALPHA_COINT, MAX_LAG_GC = 0.01, 0.50, 24
adf_p = lambda s: adfuller(s.dropna(), autolag="AIC")[1]
i1 = [c for c in data_raw.columns
      if adf_p(data_raw[c])  > ALPHA_ADF and
         adf_p(data_raw[c].diff()) < ALPHA_ADF and
         c != "Copper_Price"]

# ── 3. Cointegration filter --------------------------------------
cands = [s for s in i1
         if coint(data_raw["Copper_Price"], data_raw[s])[1] < ALPHA_COINT]

# ── 4. Granger causality tiers -----------------------------------
gc_rows = []
for s in cands:
    if data_raw[s].nunique() <= 1:  continue
    for lag in range(1, MAX_LAG_GC + 1):
        try:
            p = grangercausalitytests(
                    data_raw[["Copper_Price", s]].dropna().values,
                    maxlag=lag, verbose=False)[lag][0]["ssr_ftest"][1]
            gc_rows.append({"Series": s, "Lag": lag, "p": p})
        except Exception:
            continue
df_gc = pd.DataFrame(gc_rows)

TIERS = {0.05: [s for s in cands if df_gc.loc[df_gc["Series"] == s, "p"].min() < 0.05],
         0.10: [s for s in cands if df_gc.loc[df_gc["Series"] == s, "p"].min() < 0.10]}

# ────────────────────────────────────────────────────────────────
#  Tables 4 → 7  +  Feature Selection Results   (no CSV, no .style)
# ────────────────────────────────────────────────────────────────
from IPython.display import display
from statsmodels.tools.sm_exceptions import InfeasibleTestError

# ── Table 4 – Augmented Dickey-Fuller ----------------------------
tab4 = pd.DataFrame(
    {
        "Level p": [adf_p(data_raw[c]) for c in data_raw.columns],
        "Diff p":  [adf_p(data_raw[c].diff()) for c in data_raw.columns],
    },
    index=data_raw.columns,
).sort_values("Level p")

print("\nTable 4 – Augmented Dickey-Fuller")
display(tab4)

# Identify I(1) candidates
i1 = tab4.index[
    (tab4["Level p"] > ALPHA_ADF) & (tab4["Diff p"] < ALPHA_ADF)
]

# ── Table 5 – Engle-Granger cointegration ------------------------
rows = []
for s in i1:
    if s == "Copper_Price":
        continue
    t_stat, p_val, *_ = coint(data_raw["Copper_Price"], data_raw[s])
    rows.append({"Series": s, "t": t_stat, "p": p_val})

df_coint = pd.DataFrame(rows).set_index("Series").sort_values("p")

print("\nTable 5 – Cointegration")
display(df_coint)

cointegrated = df_coint.index[df_coint["p"] < ALPHA_COINT]

# ── Table 6 – full Granger matrix --------------------------------
gc_records = []
for s in cointegrated:
    if data_raw[s].nunique() <= 1:
        continue
    for lag in range(1, MAX_LAG_GC + 1):
        try:
            p = grangercausalitytests(
                data_raw[["Copper_Price", s]].dropna().values,
                maxlag=lag,
                verbose=False,
            )[lag][0]["ssr_ftest"][1]
            gc_records.append({"Series": s, "Lag": lag, "p": p})
        except InfeasibleTestError:
            continue

df_gc = pd.DataFrame(gc_records).sort_values(["Series", "Lag"])

print("\nTable 6 – Granger causality (all lags)")
display(df_gc)

# ── Feature Selection Results ------------------------------------
tiers = {
    a: [
        s
        for s in cointegrated
        if df_gc.loc[df_gc["Series"] == s, "p"].min() < a
    ]
    for a in TIERS_TO_BUILD
}

print("\nFeature Selection Results:")
for a in TIERS_TO_BUILD:
    print(f"\np-value < {a:.2f}: {len(tiers[a])} series")
    print(tiers[a])

# ── Table 7 – Granger-causal summary -----------------------------
summary_rows = []
for series in cointegrated:
    subset = df_gc.loc[df_gc["Series"] == series, ["Lag", "p"]]
    best    = subset.loc[subset["p"].idxmin()]
    summary_rows.append(
        {
            "Series":  series,
            "Min p":   float(best["p"]),
            "Best Lag":int(best["Lag"]),
            "p<0.01":  best["p"] < 0.01,
            "p<0.05":  best["p"] < 0.05,
            "p<0.10":  best["p"] < 0.10,
        }
    )

df_summary = pd.DataFrame(summary_rows).set_index("Series").sort_values("Min p")

print("\nTable 7 – Granger-causal summary")
display(df_summary)


# ── 5. Helper: build lag-1 feature frame --------------------------
def lag_df(feats, lag=1):
    base = {"Copper_Price": data_raw["Copper_Price"]}
    base.update({f"{f}_lag{lag}": data_raw[f].shift(lag) for f in feats})
    return pd.DataFrame(base).dropna()

# ── 6. Scenarios --------------------------------------------------
SCENARIOS = {
    "without": [],          # copper-only baseline
    "0.05"  : TIERS[0.05],
    "0.10"  : TIERS[0.10],
}

# ── 7. Model factories -------------------------------------------
MODEL_FNS = {
    "LogReg"   : lambda: make_pipeline(StandardScaler(),
                                       LogisticRegression(max_iter=1000,
                                                          random_state=42)),
    "DecTree"  : lambda: DecisionTreeClassifier(random_state=42),
    "RandForest":lambda: RandomForestClassifier(n_estimators=500,
                                                random_state=42),
    "SVM"      : lambda: make_pipeline(StandardScaler(),
                                       SVC(kernel="rbf",
                                           probability=True,
                                           random_state=42)),
}

records = []

# ── 8. Run classification for each scenario ----------------------
for scen, feats in SCENARIOS.items():
    # A. dataset
    if scen == "without":
        df = (pd.concat([data_raw["Copper_Price"],
                         data_raw["Copper_Price"].shift(1)
                                 .rename("Copper_Price_lag1")],
                        axis=1)
                .dropna())
    else:
        df = lag_df(feats, lag=1)
    # label
    df["y"] = (df["Copper_Price"].diff().shift(-1) > 0).astype(int)
    df.dropna(inplace=True)

    X, y = df.drop(columns=["Copper_Price", "y"]), df["y"]
    cut  = int(len(X) * 0.83)
    X_tr, X_te, y_tr, y_te = X.iloc[:cut], X.iloc[cut:], y.iloc[:cut], y.iloc[cut:]

    # B. supervised models
    fitted = {n: fn() for n, fn in MODEL_FNS.items()}
    for n, clf in fitted.items():
        clf.fit(X_tr, y_tr)

    # C. HMM
    rets      = df["Copper_Price"].pct_change().dropna().values.reshape(-1, 1)
    split_pt  = cut - 1
    hmm       = GaussianHMM(n_components=2, covariance_type="full",
                            n_iter=100, random_state=42).fit(rets[:split_pt])
    states    = hmm.predict(rets[split_pt:])                 # length == len(y_te)
    state_map = {s: int(mu > 0) for s, mu in enumerate(hmm.means_.flatten())}
    y_pred_hmm = pd.Series([state_map[s] for s in states[:len(y_te)]],
                           index=y_te.index)

    # D. ensembles (use KFold to satisfy cross_val_predict)
    kf = KFold(n_splits=5, shuffle=False)
    voting = VotingClassifier([(n, c) for n, c in fitted.items()],
                              voting="hard").fit(X_tr, y_tr)
    stack  = StackingClassifier([(n, c) for n, c in fitted.items()],
                                final_estimator=LogisticRegression(max_iter=1000,
                                                                    random_state=42),
                                cv=kf, n_jobs=-1).fit(X_tr, y_tr)

    # E. accuracy scores
    scores = {n: accuracy_score(y_te, c.predict(X_te)) for n, c in fitted.items()}
    scores["HMM"]    = accuracy_score(y_te, y_pred_hmm)
    scores["Voting"] = accuracy_score(y_te, voting.predict(X_te))
    scores["Stack"]  = accuracy_score(y_te, stack.predict(X_te))

    for mdl, acc in scores.items():
        records.append({"Model": mdl, "Scenario": scen, "Accuracy": acc})

# ── 9. Show comparison table -------------------------------------
acc_df = (pd.DataFrame(records)
            .pivot_table(index="Model", columns="Scenario", values="Accuracy")
            .applymap("{:.2%}".format)
            .sort_index())

print("\nAccuracy comparison – direction prediction")
display(acc_df)



Table 4 – Augmented Dickey-Fuller


Level p  Diff p
Building construction copper   0.0000  0.0000
US copper production           0.0000  0.0000
Copper mining cost             0.0000  0.0000
Commodity speculation          0.0000  0.0000
Chile copper production        0.0000  0.0000
...                               ...     ...
COVID                          0.7920  0.0000
Terrorist attack               0.8097  0.0000
Electronics manufacturing      0.8776  0.0000
China US trade tensions        0.9989  0.0002
Copper tariff                  1.0000  0.0000

[98 rows x 2 columns]


Table 5 – Cointegration


t      p
Series                                  
Iran Iraq War             -2.8943 0.1375
5G technology             -2.8166 0.1605
Electronics manufacturing -2.7911 0.1685
Copper ore reserves       -2.7675 0.1762
Currency exchange rates   -2.7040 0.1981
Copper concentrate        -2.6545 0.2164
Middle East conflicts     -2.6240 0.2281
Mining sanctions          -2.5874 0.2420
Yahoo finance             -2.5775 0.2460
RMB exchange rate         -2.5758 0.2467
Energy crisis             -2.5618 0.2525
Scrap copper prices       -2.5581 0.2541
Manufacturing PMI         -2.5548 0.2554
COVID                     -2.5403 0.2616
Extreme weather           -2.5326 0.2649
Euro exchange rate        -2.5289 0.2665
Copper tariff             -2.5263 0.2676
China US trade tensions   -2.5121 0.2738
COVID copper              -2.5116 0.2740
Electric vehicle demand   -2.4723 0.2914
Bloomberg                 -2.3920 0.3286
Copper price forecast     -2.3662 0.3410
Terrorist attack          -2.3257 0.3608
Trade war                 -2.3010 0.3731
Global GDP growth         -2.2684 0.3894
World GDP by country      -2.2533 0.3970
Inflation expectations    -2.2304 0.4087


Table 6 – Granger causality (all lags)


Series  Lag      p
24   5G technology    1 0.9159
25   5G technology    2 0.4953
26   5G technology    3 0.4765
27   5G technology    4 0.5444
28   5G technology    5 0.3709
..             ...  ...    ...
211  Yahoo finance   20 0.1242
212  Yahoo finance   21 0.1664
213  Yahoo finance   22 0.2101
214  Yahoo finance   23 0.2764
215  Yahoo finance   24 0.3186

[648 rows x 3 columns]


Feature Selection Results:

p-value < 0.01: 6 series
['Copper ore reserves', 'Mining sanctions', 'Extreme weather', 'Euro exchange rate', 'Copper tariff', 'Terrorist attack']

p-value < 0.05: 12 series
['Iran Iraq War', 'Electronics manufacturing', 'Copper ore reserves', 'Mining sanctions', 'Yahoo finance', 'Scrap copper prices', 'Extreme weather', 'Euro exchange rate', 'Copper tariff', 'China US trade tensions', 'Terrorist attack', 'Trade war']

p-value < 0.10: 13 series
['Iran Iraq War', 'Electronics manufacturing', 'Copper ore reserves', 'Middle East conflicts', 'Mining sanctions', 'Yahoo finance', 'Scrap copper prices', 'Extreme weather', 'Euro exchange rate', 'Copper tariff', 'China US trade tensions', 'Terrorist attack', 'Trade war']

Table 7 – Granger-causal summary


Min p  Best Lag  p<0.01  p<0.05  p<0.10
Series                                                            
Extreme weather           0.0007         7    True    True    True
Terrorist attack          0.0008        15    True    True    True
Euro exchange rate        0.0024         9    True    True    True
Copper tariff             0.0040         6    True    True    True
Copper ore reserves       0.0044        21    True    True    True
Mining sanctions          0.0057        24    True    True    True
Trade war                 0.0121         9   False    True    True
Scrap copper prices       0.0196        21   False    True    True
China US trade tensions   0.0263         1   False    True    True
Yahoo finance             0.0356        15   False    True    True
Electronics manufacturing 0.0371         2   False    True    True
Iran Iraq War             0.0394         6   False    True    True
Middle East conflicts     0.0580         8   False   False    True
Copper concentrate        0.1174        15   False   False   False
COVID                     0.1325        23   False   False   False
Currency exchange rates   0.1420         1   False   False   False
Global GDP growth         0.1694        16   False   False   False
COVID copper              0.1707        23   False   False   False
Inflation expectations    0.2726         6   False   False   False
RMB exchange rate         0.2776        15   False   False   False
Manufacturing PMI         0.3599         1   False   False   False
Bloomberg                 0.3698        17   False   False   False
5G technology             0.3709         5   False   False   False
World GDP by country      0.4347         3   False   False   False
Energy crisis             0.5680         5   False   False   False
Copper price forecast     0.7506         6   False   False   False
Electric vehicle demand   0.7906         2   False   False   False


Accuracy comparison – direction prediction


Scenario      0.05    0.10 without
Model                             
DecTree     46.67%  57.78%  46.67%
HMM         55.56%  55.56%  55.56%
LogReg      44.44%  48.89%  51.11%
RandForest  46.67%  44.44%  46.67%
SVM         51.11%  48.89%  62.22%
Stack       44.44%  40.00%  55.56%
Voting      48.89%  48.89%  46.67%